## LWIR Filters Distortion
When capturing real-world scenes using TAU2, an unexpected and unclear spherical distortion appears when applying an IR filter.
This artifact only appears when applying a filter, as can be seen from the following example:

In [1]:
from tools import calc_rx_power
import plotly.express as px
from plotly.subplots import make_subplots
import numpy as np
from pathlib import Path
%load_ext autoreload
%autoreload 2

data_base_dir = Path(
    r"C:\Users\omriber\Documents\Thesis\MultiSpectralCtrl\download")

data_fname = "cnt1_20210830_h15m53s38.npy"
data = np.load(Path(data_base_dir, data_fname))

fig = make_subplots(1, 2)
fig = px.imshow(data[0, 0], color_continuous_scale='gray',
                title="Pan-Chromatic")

fig.show()
fig = px.imshow(data[1, 0], color_continuous_scale='gray', title="Filter1")
fig.show()


While seemingly similar to vignetting, it's clearly not, as in opposed to vignetting, the center is brighter than the edges (in vignetting its vice-versa). 

Moreover, many pixels have a higher intensity level when the filter is applied, in contrast to the expected physical phenomenon, by which the grey level is proportional to the radiated power. This can be clearly observed when using the same dynamic range for showing both images:

In [ ]:
fig = px.imshow(data[:2, 0, ...], facet_col=0,
                color_continuous_scale='gray')
fig.layout.annotations[0].text="Pan-Chromatic"
fig.layout.annotations[1].text="Filtered"
fig.show()


This unexpected bias difference in favor of the filtered version might be due to the filter acting as a black-body, radiating towards the bolumetric sensor due to it's temperature and relatively high proximity to the sensor.

While unexpected, this is not necessarily an issue, as we don't necessarily intend to cancel it out, but rather characterize it in order to be able to predict it and use it to simulate the filtered scene given the pan-chromatic one.

In either way, in order to have a good estimate of the filtered image (given a pan-chromatic one), we need to come up with the model for the obtained distortion.

### Estimation Workflow:
In order to predict how a filtered scene should look given its panchromatic conterpart, we need to:
1. Fit a model for estimating the pixel-wise temperature map given a pan-chromatic scene (due to its relatively high SNR).
2. Fit a model for estimating the grey-levels of filtered images given the radiance of the scene.
3. Use Plank's black-body radiation and the physics of the filters to estimate the radiance given an input temperature
4. Combine the components to a pipeline which takes a pan-chromatic image as input and predicts it's filtered version. 

This notebook should be run after having run both the <em>temperature_calib</em> and <em>filters_calib</em>, which are used to fit the models described in steps 1-2.
Phase 3 is already implemented in the function <em>calc_rx_power</em>. This notebook will focus on phase 4 and evaluating its outcomes.


### Packages and data imports:

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import matplotlib
import numpy as np
from tools import calc_rx_power, get_measurements, FilterWavelength, FilterWavelength, choose_random_pixels, calc_r2, c2k, k2c, find_parent_dir
from plots import showFacetImages, plot_rand_pix_regress
from regression import GlRegressor
import sys
from pathlib import Path
sys.path.append(str(Path().cwd().parent))


%load_ext autoreload
%autoreload 2
%matplotlib widget


matplotlib.rcParams.update({'font.size': 14})

path_to_files = find_parent_dir("rawData") / 'calib' / 'tlinear_0'
path_to_models = find_parent_dir("models")


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Models imports:

For manual inspection, we'll begin with estimating the 9nm scene:

In [3]:
def load_model(model_name):
    f_name = model_name + ".pkl"
    model = GlRegressor()
    model.load_model(path_to_models / f_name)
    return model

filt = FilterWavelength.nm9000
temperature_to_pan = load_model("t2gl_4ord")
power_to_filt = load_model(f"p2gl_{filt.name}")


### Construct the PipeLine

In [4]:
def colorization_pipeline(pan_image):
    temperature_map = temperature_to_pan.predict(pan_image, is_inverse=True)
    power_map = calc_rx_power(temperature=k2c(temperature_map), filt=filt)
    filt_image = power_to_filt.predict(power_map)
    return filt_image

### Manually inspect the pipeline's results:

In [5]:
filt_image = colorization_pipeline(data[0, 0])
